<a href="https://colab.research.google.com/github/alfrepereyra/laboratorio/blob/main/laboratorio.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

todas las importaciones que usamos

In [86]:
from google.colab import drive
drive.mount('/content/drive')
import pandas as pd
from geopy.geocoders import Nominatim
import plotly.express as px
import plotly.graph_objects as go
import os
from geopy.geocoders import Nominatim


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [55]:
pip install geopy


**tradujimos las columnas del dataframe**

In [ ]:

traducciones = {
    'Order ID': 'ID de Pedido',
    'Product': 'Producto',
    'Quantity Ordered': 'Cantidad Pedida',
    'Price Each': 'Precio Unitario',
    'Order Date': 'Fecha de Pedido',
    'Purchase Address': 'Dirección de Envio'

}



# Cargar el DataFrame original desde el archivo CSV
ruta_de_archivos =  '/content/drive/MyDrive/UPSO/Dataset de ventas2'
archivos = os.listdir(ruta_de_archivos)

dataframes= {}

for archivo in archivos:
    if archivo.endswith('.csv'):  # Asegurarse de que solo se consideren archivos CSV
        mes = archivo.split('_')[3].split('.')[0]  # Obtener el nombre del archivo sin la extensión
        ruta_completa = os.path.join(ruta_de_archivos, archivo)  # Ruta completa al archivo
        df = pd.read_csv(ruta_completa)
        # Cambiar los nombres de las columnas según las traducciones
        df_traducido = df.rename(columns=traducciones)

        # Guardar el DataFrame traducido en un nuevo archivo CSV
        ruta_archivo_traducido =  f'/content/drive/MyDrive/UPSO/Dataset_deventas_{mes}.csv'
        df_traducido.to_csv(ruta_archivo_traducido, index=False,mode='w')  # index=False para no guardar el índice en el CSV

df_traducido


**cargamos el nuevo dataframe traducido y le hacemos una limpieza de los datos**

In [58]:
ruta_de_archivos = '/content/drive/MyDrive/UPSO/Dataset de ventas2'



ruta_de_archivos = '/content/drive/MyDrive/UPSO/Dataset de ventas2'
archivos = os.listdir(ruta_de_archivos)

dataframes= {}

for archivo in archivos:
    if archivo.endswith('.csv'):  # Asegurarse de que solo se consideren archivos CSV
        mes = archivo.split('_')[3].split('.')[0]  # Obtener el nombre del archivo sin la extensión
        ruta_completa = os.path.join(ruta_de_archivos, archivo)  # Ruta completa al archivo
        df = pd.read_csv(ruta_completa)  # Cargar el archivo CSV en un DataFrame
        df_ventas = df.copy()

        df_ventas['Cantidad Pedida'] = pd.to_numeric(df_ventas['Cantidad Pedida'], errors='coerce')  #El errors= 'coerce' transforma los valores no numericos a NaN'
        df_ventas['Precio Unitario'] = pd.to_numeric(df_ventas['Precio Unitario'], errors='coerce')


        df_ventas = df_ventas.loc[~df_ventas['Cantidad Pedida'].isna()]
        df_ventas = df_ventas.loc[~df_ventas['Precio Unitario'].isna()]

        # Elimino todos los Nan y me quedo solo con los valores numericos
        df_ventas = df_ventas.dropna()

        # Transformo todos los valores numericos al tipo de dato int
        df_ventas['Cantidad Pedida'] = df_ventas['Cantidad Pedida'].astype(int)
        df_ventas['Precio Unitario'] = df_ventas['Precio Unitario'].astype(int)

        dataframes[mes] = df_ventas  # Agregar el DataFrame al diccionario usando el nombre del mes

In [59]:

meses = ['Enero', 'Febrero', 'Marzo', 'Abril', 'Mayo', 'Junio',
        'Julio', 'Agosto', 'Septiembre', 'Octubre', 'Noviembre', 'Diciembre']

for mes in meses:
    dataframe_mes = dataframes[mes]

#CRACION DE DATAFRAME MES CON LAS COLUMNAS DE HORA DIA MES Y UNA FUNCION QUE ME AYUDA A EXTRAER DATOS DE EL DATAFRAME
def extraer_datos(datos):
  datos['Fecha de Pedido'] = pd.to_datetime(datos['Fecha de Pedido'])
  datos['Hora'] = datos['Fecha de Pedido'].dt.hour
  datos['Dia'] = datos['Fecha de Pedido'].dt.day
  datos['Mes'] = datos['Fecha de Pedido'].dt.month
  return datos

dataframe_mes = extraer_datos(dataframe_mes)


#CREACION DEL DATAFRAME ANUAL CON LAS VENTAS DE TODOS LOS MESES SUMADAS QUE USAMOS MAS ADELANTE
dataframes_meses = [dataframes[mes] for mes in meses]

# Crear un DataFrame para todo el año
df_anual = pd.concat(dataframes_meses, ignore_index=True)



# 1. Comportamiento de las ventas en los distintos meses:

###¿Cómo variaron las ventas a lo largo de los diferentes meses?

In [60]:

# Creo listas para almacenar los totales de ventas y los nombres de los meses
totales_ventas = []
nombres_meses = []

for mes in meses:
    dataframe_mes = dataframes[mes]
    dataframe_mes = extraer_datos(dataframe_mes)

    total_ventas_mes = dataframe_mes['Cantidad Pedida'].sum()
    totales_ventas.append(total_ventas_mes)
    nombres_meses.append(mes)

# Creo el objeto figura con el gráfico de barras
fig = go.Figure()

fig.add_trace(go.Bar(
    x=nombres_meses,
    y=totales_ventas,
    marker=dict(color=totales_ventas, colorscale = 'RdYlGn', colorbar=dict(title="Total de ventas", x=1.0, thickness=15)),  # Color y barra de colores
    text=totales_ventas,
    textposition='auto',

))


fig.update_layout(
    title="Total de ventas por mes",
    xaxis=dict(title="Mes"),
    yaxis=dict(title="Total de ventas"),
)

fig.show()


### ¿Hubo algún mes que se destacó en términos de ventas?



### ¿Cuál es el ingreso total generado por mes?


In [61]:
# Creo listas vacias para almacenar las ganancias totales y los nombres de los meses
ganancias_totales = []
nombres_meses = []

for mes in meses:
    dataframe_mes = dataframes[mes]
    dataframe_mes = extraer_datos(dataframe_mes)

    # Calcular las ganancias del mes multiplicando la cantidad pedida por el precio unitario y sumando todos los productos vendidos
    ganancias_mes = (dataframe_mes['Cantidad Pedida'] * dataframe_mes['Precio Unitario']).sum()
    ganancias_totales.append(ganancias_mes)
    nombres_meses.append(mes)


fig = go.Figure()

fig.add_trace(go.Bar(
    x=nombres_meses,
    y=ganancias_totales,
    marker=dict(color=ganancias_totales, colorscale='RdYlGn', colorbar=dict(title="Ganancias Totales", x=1.0, thickness=15)),
    text=ganancias_totales,
    textposition='auto',
))


fig.update_layout(
    title="Ganancias Totales por Mes",
    xaxis=dict(title="Mes"),
    yaxis=dict(title="Ganancias Totales"),
)

fig.show()

# 2. Optimización de la publicidad y patrón de ventas por hora:


##¿Cuál es el momento ideal del día para presentar la publicidad y aumentar la
##probabilidad de compra?

In [62]:

Horas = list(range(24))

# Creo el objeto figura
fig = go.Figure()
horas_analizadas = [19, 12, 16]

for hora in horas_analizadas:
    total_productos_vendidos = []

    for mes in meses:
        dataframe_mes = dataframes[mes]
        dataframe_mes = extraer_datos(dataframe_mes)  # Reemplaza esto con el procesamiento que necesites

        ventas_hora = dataframe_mes[dataframe_mes['Hora'] == hora]

        # Calcular la cantidad total de productos vendidos para la hora actual
        total_productos_vendidos.append(ventas_hora['Cantidad Pedida'].sum())

    # Agrego al objeto figura un gráfico de línea con las horas y las ventas por hora
    fig.add_trace(go.Scatter(
        x=meses,
        y=total_productos_vendidos,
        mode='lines',
        name=f'{hora} horas',
        line=dict(width=2, shape='spline'),
    ))

# Configuro los ejes y los títulos
fig.update_layout(
    title="Unidades vendidas por hora",
    xaxis=dict(title="Meses", tickvals=Horas),
    yaxis=dict(title="Unidades vendidas", side="left"),
    legend=dict(y=0.3, yanchor='bottom'),
)

fig.show()

 ## ¿Cómo cambian los patrones de ventas por hora a lo largo del año?

In [63]:

Horas = list(range(24))

# Creo el objeto figura
fig = go.Figure()

for mes in meses:
    dataframe_mes = dataframes[mes]
    dataframe_mes = extraer_datos(dataframe_mes)  # Reemplaza esto con el procesamiento que necesites
    Ventas_por_hora = dataframe_mes.groupby('Hora')['Cantidad Pedida'].sum()



    # Agrego al objeto figura un gráfico de línea con las horas y las ventas por hora
    fig.add_trace(go.Scatter(
        x=Horas,
        y=Ventas_por_hora,
        mode='lines',
        name=mes,
        line=dict(width=2,shape='spline'),
    ))

# Configuro los ejes y los títulos
fig.update_layout(
    title="Unidades vendidas por hora en diferentes meses",
    xaxis=dict(title="Hora", tickvals=Horas),
    yaxis=dict(title="Unidades vendidas", side="left"),
    legend=dict(y=0.3, yanchor='bottom'),
)

fig.show()


## ¿Hay modificaciones en los patrones de ventas durante las horas de mayor actividad
##en los distintos meses?

# 3. Distribución de ventas por ubicación

##En qué ciudades se han registrado las mayores ventas?

In [64]:
diccionario_ordenado = {}

for mes in meses:
    if mes in dataframes:
        dataframe_mes = dataframes[mes]  # Obtener el DataFrame correspondiente al mes


        direccion_split = dataframe_mes["Dirección de Envio"].str.split(',')
        dataframe_mes["Ciudad"] = direccion_split.str[1].str.strip()


        ventas_ciudades = dataframe_mes.groupby("Ciudad")["Cantidad Pedida"].sum().reset_index()


        diccionario_ordenado[mes] = ventas_ciudades

df_resultado = pd.concat(diccionario_ordenado.values())

# Sumar todas las ciudades y la cantidad pedida
total_ventas = df_resultado.groupby("Ciudad")["Cantidad Pedida"].sum().reset_index()


total_ventas

Ciudad  Cantidad Pedida
0        Atlanta            16602
1         Austin            11153
2         Boston            22528
3         Dallas            16730
4    Los Angeles            33289
5  New York City            27932
6       Portland            14053
7  San Francisco            50239
8        Seattle            16553

In [65]:

diccionario_ordenado = {}

for mes in meses:
    if mes in dataframes:
        dataframe_mes = dataframes[mes]  # Obtener el DataFrame correspondiente al mes

        # Separar la columna "Dirección de Envio" en "Ciudad"
        direccion_split = dataframe_mes["Dirección de Envio"].str.split(',')
        dataframe_mes["Ciudad"] = direccion_split.str[1].str.strip()

        # Calcular la suma de ventas por ciudad
        ventas_ciudades = dataframe_mes.groupby("Ciudad")["Cantidad Pedida"].sum().reset_index()

        # Almacenar el resultado en el diccionario
        diccionario_ordenado[mes] = ventas_ciudades

df_resultado = pd.concat(diccionario_ordenado.values())

# Sumar todas las ciudades y la cantidad pedida
total_ventas = df_resultado.groupby("Ciudad")["Cantidad Pedida"].sum().reset_index()





dataframe_mapa = pd.DataFrame({
    'Latitud': [33.7490, 30.2672, 42.3601, 32.7767, 34.0522, 40.7128, 45.5051, 37.7749, 47.6062],
    'Longitud': [-84.3880, -97.7431, -71.0589, -96.7970, -118.2437, -74.0060, -122.6750, -122.4194, -122.3321],

})

dataframe_mapa['Ciudad'] = total_ventas['Ciudad']
dataframe_mapa['Cantidad Pedida'] = total_ventas['Cantidad Pedida']


fig = px.scatter_geo(dataframe_mapa,
                     lat="Latitud",
                     lon="Longitud",
                     text="Ciudad",
                     size="Cantidad Pedida",
                     color="Cantidad Pedida",
                     hover_name="Ciudad",
                     projection="albers usa"
                    )

fig.update_geos(
    scope="usa",
    visible=False,
    showcoastlines=True
)

fig.update_layout(
    title="Ciudades Marcadas por Ventas en Estados Unidos",
    geo=dict(
        showland=True,
    )
)

fig.show()

##Cómo se comparan las ventas en diferentes estados o regiones?

In [79]:

def extraer_datos(datos):
    direccion_split = datos["Dirección de Envio"].str.split(',')
    datos["Estado"] = direccion_split.str[-1].str.strip()
    return datos

# Extrae los datos
codigos_postales1 = extraer_datos(df_anual)
codigos_postales = codigos_postales1['Estado'].unique()

# Inicializa el geocodificador
geolocalizador = Nominatim(user_agent="mi_aplicacion", timeout=10)

coordenadas_dict = {}

# Itera sobre los códigos postales y obtén las coordenadas
for codigo_postal in codigos_postales:
    location = geolocalizador.geocode(codigo_postal + ", USA")
    if location:
        coordenadas_dict[codigo_postal] = (location.longitude, location.latitude)
    else:
        coordenadas_dict[codigo_postal] = (None, None)

#Calcular las ventas por estado y agruparlas

ventas_por_estado = df_anual.groupby('Estado')['Cantidad Pedida'].sum().reset_index()

#Cambiar el nombre de la columna 'ciudades' a 'estados'

ventas_por_estado.columns = ['Estados', 'Ventas']

#Combinar las ventas con las coordenadas
ventas_por_estado['lon'], ventas_por_estado['lat'] = zip(*ventas_por_estado['Estados'].map(coordenadas_dict))


fig = go.Figure(data=[go.Table(
    header=dict(values=["Estado", "Ventas"]),
    cells=dict(values=[ventas_por_estado['Estados'], ventas_por_estado['Ventas']]))
])


fig.update_layout(
    title="Ventas por Estado",
)

fig.show()


##Existe variación en las ventas por estado a lo largo de los meses? (falta enero)
estoy intentando que agregue enero descucbri es la funcion .unique() que si la sacas aparece enero pero se pone borrosas las barras no supimos como arreglarlo


In [69]:
import pandas as pd
import plotly.express as px


meses = ['Enero', 'Febrero', 'Marzo', 'Abril', 'Mayo', 'Junio',
        'Julio', 'Agosto', 'Septiembre', 'Octubre', 'Noviembre', 'Diciembre']


dataframes_meses = []

def extraer_datos(datos):
    datos['Fecha de Pedido'] = pd.to_datetime(datos['Fecha de Pedido'])
    datos['Mes'] = datos['Fecha de Pedido'].dt.month


    direccion_split = datos["Dirección de Envio"].str.split(',')
    datos["Estado"] = direccion_split.str[2].str.strip()

    return datos

for mes in meses:
    dataframe_mes = dataframes[mes]
    dataframe_mes = extraer_datos(dataframe_mes)
    dataframes_meses.append(dataframe_mes)

datos = pd.concat(dataframes_meses, ignore_index=True)

#Agrupar por Estado y Mes, y sumar la cantidad pedida
ventas_por_estado_mes = datos.groupby(['Estado', 'Mes'])['Cantidad Pedida'].sum().reset_index()

#Calcular la variación de las ventas entre meses
ventas_por_estado_mes['Variación'] = ventas_por_estado_mes.groupby('Estado')['Cantidad Pedida'].pct_change() * 100

#Grafico la variación de las ventas
fig = px.bar(ventas_por_estado_mes, x='Mes', y='Variación', color='Estado',
             labels={'Variación': 'Variación de Ventas (%)'},
             title='Variación de Ventas por Estado a lo largo de los Meses')
fig.show()

In [70]:
import pandas as pd
import plotly.express as px

#Extraer datos y combinar en un solo DataFrame
def extraer_datos(datos):
    datos['Fecha de Pedido'] = pd.to_datetime(datos['Fecha de Pedido'])
    datos['Mes'] = datos['Fecha de Pedido'].dt.month


    direccion_split = datos["Dirección de Envio"].str.split(',')
    datos["Estado"] = direccion_split.str[2].str.strip()

    return datos


df_anual = extraer_datos(df_anual)

#Agrupar por Estado y Mes, y sumar la cantidad pedida
ventas_por_estado_mes = df_anual.groupby(['Estado', 'Mes'])['Cantidad Pedida'].sum().reset_index()


estados = ventas_por_estado_mes['Estado']
meses = range(1, 13)  # Considerar los meses del 1 al 12

combinaciones_estado_mes = [(estado, mes) for estado in estados for mes in meses]
ventas_por_estado_mes = ventas_por_estado_mes.set_index(['Estado', 'Mes']).reindex(combinaciones_estado_mes, fill_value=0).reset_index()

ventas_por_estado_mes['Variación'] = ventas_por_estado_mes.groupby('Estado')['Cantidad Pedida'].pct_change() * 100


fig = px.bar(ventas_por_estado_mes, x='Mes', y='Variación', color='Estado',
             labels={'Variación': 'Variación de Ventas (%)'},
             title='Variación de Ventas por Estado a lo largo de los Meses')
fig.show()

#4. Análisis del producto más vendido:

##¿Cuál es el producto más vendido en general y en cada mes?

**ESTOS SON LOS PRODUCTOS MAS VENDIDOS EN GENERAL EN UNA TABLA DE PORCENTAJES**

In [71]:
import plotly.express as px
import pandas as pd


fig = px.pie(df_anual,
             names='Producto',
             values='Cantidad Pedida',
             title='Ventas Anuales por Producto')

fig.show()



**ESTOS SON LOS PRODUCTOS MAS EN CADA MES EN UNA TABLA DE BARRAS**

In [78]:

meses_mas_vendidos = []
productos_mas_vendidos = []
cantidades_mas_vendidas = []

diccionario_ordenado = {}


for mes in meses:
    if mes in dataframes:
        diccionario_ordenado[mes] = dataframes[mes]


for mes in diccionario_ordenado :
    dataframe_mes = diccionario_ordenado[mes]

    # Agrupar el DataFrame por "Producto" y sumar las cantidades pedidas
    ventas_por_producto = dataframe_mes.groupby("Producto")["Cantidad Pedida"].sum()

    # Encontrar el producto más vendido en este mes
    producto_mas_vendido = ventas_por_producto.idxmax()
    cantidad_mas_vendida = ventas_por_producto.max()

    # Agregar los resultados a las listas
    meses_mas_vendidos.append(mes)
    productos_mas_vendidos.append(producto_mas_vendido)
    cantidades_mas_vendidas.append(cantidad_mas_vendida)


fig = go.Figure()

fig.add_trace(go.Bar(
    x=meses_mas_vendidos,
    y=cantidades_mas_vendidas,
    text=productos_mas_vendidos,
    textposition='auto',

))


fig.update_layout(
    title="Total de ventas por mes",
    xaxis=dict(title="Mes"),
    yaxis=dict(title="Total de ventas"),
)

fig.show()

 ## ¿Qué factores crees que han contribuido al éxito de ese producto en particular?

# Tendencia ventas:

 ## ¿Existe alguna tendencia o patrón en las ventas que se repita a lo largo  ##
 ## de los días en los diferentes meses?

In [73]:

# Lista de meses
meses = ['Enero', 'Febrero', 'Marzo', 'Abril', 'Mayo', 'Junio',
        'Julio', 'Agosto', 'Septiembre', 'Octubre', 'Noviembre', 'Diciembre']

# Crear el objeto figura
fig = go.Figure()

# Dataframes con datos de ventas por mes
dataframes_meses = [dataframes[mes] for mes in meses]

# Crear un DataFrame para todo el año
df_anual = pd.concat(dataframes_meses, ignore_index=True)

# Añadir una nueva columna 'Mes' al DataFrame df_anual
df_anual['Mes'] = df_anual['Fecha de Pedido'].dt.month

# Agrupar el DataFrame por mes y día y calcular la suma de las ventas para cada día
ventas_por_dia_mes = df_anual.groupby(['Mes', 'Dia'])['Cantidad Pedida'].sum().reset_index()

# Generar el gráfico de líneas
for mes in meses:
    mes_numero = meses.index(mes) + 1
    ventas_mes = ventas_por_dia_mes[ventas_por_dia_mes['Mes'] == mes_numero]
    fig.add_trace(go.Scatter(
        x=ventas_mes['Dia'],
        y=ventas_mes['Cantidad Pedida'],
        mode='lines',
        name=mes,
        line=dict(width=2, shape='spline'),
    ))

# Configurar los ejes y los títulos
fig.update_layout(
    title="Tendencia de Ventas por Día en Diferentes Meses",
    xaxis=dict(title="Día"),
    yaxis=dict(title="Ventas", side="left"),
    legend=dict(y=0.3, yanchor='bottom'),
)


##¿Cómo varían las ventas a lo largo de los diferentes días de la semana?

In [74]:


df_anual['Fecha de Pedido'] = pd.to_datetime(df_anual['Fecha de Pedido'])
df_anual['Día de la Semana'] = df_anual['Fecha de Pedido'].dt.day_name()

# Calcular el total de ventas por día de la semana
ventas_por_dia_semana = df_anual.groupby('Día de la Semana')['Cantidad Pedida'].sum().reset_index()

# Define un diccionario de colores para los días de la semana
colores = {
    'Monday': 'blue',
    'Tuesday': 'blue',
    'Wednesday': 'blue',
    'Thursday': 'blue',
    'Friday': 'blue',
    'Saturday': 'green',
    'Sunday': 'green'
}

# Crea el gráfico de barras
fig = px.bar(ventas_por_dia_semana,
             x='Día de la Semana',
             y='Cantidad Pedida',
             color='Día de la Semana',
             color_discrete_map=colores,
             labels={'Cantidad Pedida': 'Ventas Totales'},
             title='Ventas Totales por Día de la Semana',
             text='Cantidad Pedida')

# Personaliza el diseño del gráfico
fig.update_layout(xaxis_title='Día de la Semana', yaxis_title='Ventas Totales')
fig.show()

##Se observa alguna diferencia significativa en las ventas entre los días laborables y los fines de semana?


# Impacto de eventos especiales en las ventas:


##¿Se ha observado algún aumento o disminución significativa en las ventas en día cercanos a eventos especiales, como días festivos?

In [75]:


# Convierte la columna 'Fecha de Pedido' en un objeto de fecha y hora:
df_anual['Fecha de Pedido'] = pd.to_datetime(df_anual['Fecha de Pedido'], errors='coerce')

#Elimina filas con fechas nulas o no válidas en 'Fecha de Pedido'
df_anual = df_anual.dropna(subset=['Fecha de Pedido'])

#Asegúrate de que todas las fechas estén en formato de fecha (sin hora)
df_anual['Fecha de Pedido'] = df_anual['Fecha de Pedido'].dt.date

#Define las fechas festivas y el número de días que las rodean
fechas_festivas = {
    'Navidad': '2019-12-25',
    'Año Nuevo': '2019-01-01',
    'Día de los enamorados': '2019-02-14',
    'Halloween': '2019-10-31'
}

dias_cercanos = 4

for festividad, fecha in fechas_festivas.items():
    fecha_festividad = pd.to_datetime(fecha).date()
    fecha_inicio = fecha_festividad - pd.DateOffset(days=dias_cercanos)
    fecha_fin = fecha_festividad + pd.DateOffset(days=dias_cercanos)

    #Filtrar los datos para el rango de fechas
    df_festividad = df_anual[(df_anual['Fecha de Pedido'] >= pd.Timestamp(fecha_inicio)) & (df_anual['Fecha de Pedido'] <= pd.Timestamp(fecha_fin))]

    #Calcular las ventas sumando las cantidades pedidas para cada día
    ventas_por_dia = df_festividad.groupby('Fecha de Pedido')['Cantidad Pedida'].sum().reset_index()

    #Crear un gráfico de barras
    fig = go.Figure()
    fig.add_trace(go.Bar(x=ventas_por_dia['Fecha de Pedido'], y=ventas_por_dia['Cantidad Pedida']))


    fig.update_layout(title=f'Ventas cerca de {festividad}',
                      xaxis_title='Fecha',
                      yaxis_title='Ventas',
                      xaxis_tickangle=-45)

    fig.show()

<ipython-input-75-d0a6b528c20f>:30: FutureWarning:

Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior. In a future version these will be considered non-comparable. Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.



<ipython-input-75-d0a6b528c20f>:30: FutureWarning:

Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior. In a future version these will be considered non-comparable. Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.



<ipython-input-75-d0a6b528c20f>:30: FutureWarning:

Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior. In a future version these will be considered non-comparable. Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.



<ipython-input-75-d0a6b528c20f>:30: FutureWarning:

Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior. In a future version these will be considered non-comparable. Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.



##¿Qué eventos específicos han tenido un impacto notable en el comportamiento de las ventas y cómo se manifestó ese impacto?

In [88]:

#Multiplica la cantidad pedida por el precio unitario para obtener el total de ventas por fila
df_anual['Total de Ventas'] = df_anual['Cantidad Pedida'] * df_anual['Precio Unitario']

#Agrupa los datos por día y suma los totales de ventas en cada día
ventas_por_dia = df_anual.groupby('Fecha de Pedido')['Total de Ventas'].sum().reset_index()

#Ordena el DataFrame en orden descendente según el total de ventas
ventas_por_dia = ventas_por_dia.sort_values(by='Total de Ventas', ascending=False)

#Obtiene los 5 días con los mayores ingresos
top_5_dias_ventas = ventas_por_dia.head(5)

# Gráfica los 5 días con mayores ingresos usando Plotly Express
fig = px.bar(top_5_dias_ventas, x='Fecha de Pedido', y='Total de Ventas', title='Top 5 Días con Mayores Ingresos')
fig.show()